In [59]:
# Import necessary libraries

import pandas as pd
import plotly.express as px
import altair as alt
import datetime
from scipy.stats import pearsonr

In [4]:
# Reading in file and displaying generel information
car_sales_df = pd.read_csv(
    "/Users/deanpierrot/Desktop/Repos/streamlit_car_cales_adver/vehicles_us.csv"
)

car_sales_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [7]:
# Check for duplicates in the dataframe
duplicate_rows = car_sales_df.duplicated()

# Display a warning if duplicates are found
if duplicate_rows.any():
    print("Warning: Duplicate rows found in the dataset.")
    print("Number of duplicate rows:", duplicate_rows.sum())
else:
    print("No duplicates found.")

No duplicates found.


In [11]:
# Check for missing values in the 'cylinders' column
missing_cylinders = car_sales_df["cylinders"].isnull().sum()

# Display the number of missing values
print("Missing values in 'cylinders' column:", missing_cylinders)


Missing values in 'cylinders' column: 3645


In [13]:
# Fill missing values using groupby with a custom function
def fill_missing_median(group):
    non_null_values = group.dropna()
    if non_null_values.empty:
        return group
    else:
        median_value = non_null_values.median()
        return group.fillna(median_value)


car_sales_df["cylinders"] = car_sales_df.groupby(["model", "model_year"])[
    "cylinders"
].transform(fill_missing_median)

# Display information about the filled missing values
print("\nAfter Filling Missing Values in 'cylinders' column:")
print(car_sales_df.info())


After Filling Missing Values in 'cylinders' column:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     47880 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB
None


In [15]:
display(car_sales_df.sample(5))

price  model_year                       model  condition  cylinders  \
20810   7000      2010.0            chevrolet malibu  excellent        4.0   
29893   4995      2004.0                    ram 1500  excellent        8.0   
17849   3200      1997.0                  ford f-150       good        8.0   
45907  11950      2011.0  jeep grand cherokee laredo  excellent        6.0   
49623   8995      2009.0          chevrolet suburban       good        8.0   

      fuel  odometer transmission    type paint_color  is_4wd date_posted  \
20810  gas   73000.0    automatic   sedan       white     NaN  2018-08-06   
29893  gas  194193.0    automatic  pickup      silver     1.0  2018-10-19   
17849  gas  127000.0    automatic   truck         red     NaN  2018-06-12   
45907  gas  126337.0    automatic     SUV       black     1.0  2018-08-06   
49623  gas  211766.0    automatic     SUV       white     1.0  2019-02-13   

       days_listed  
20810           96  
29893           66  
17849           49  
45907           23  
49623           14

**Issues & Fixes:** <br>
**model_year** and **cylinders** are represented as float64, but they could potentially be converted to integers since model years and the number of cylinders are typically whole numbers.<br>
**odometer** is represented as float64, but it could be converted to an integer for simplicity.<br>
**date_posted** is represented as a object, converting it to a datetime data type will alow for easier handling of date-related operations.<br>
**Missing values** dropping those from the dataset.

In [17]:
# Convert data types
car_sales_df["model_year"] = car_sales_df["model_year"].astype(
    "Int64"
)  # Convert to nullable integer
car_sales_df["odometer"] = car_sales_df["odometer"].astype(
    "Int64"
)  # Convert to nullable integer
car_sales_df["date_posted"] = pd.to_datetime(car_sales_df["date_posted"])


In [18]:
car_sales_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         51525 non-null  int64         
 1   model_year    47906 non-null  Int64         
 2   model         51525 non-null  object        
 3   condition     51525 non-null  object        
 4   cylinders     47880 non-null  float64       
 5   fuel          51525 non-null  object        
 6   odometer      43633 non-null  Int64         
 7   transmission  51525 non-null  object        
 8   type          51525 non-null  object        
 9   paint_color   42258 non-null  object        
 10  is_4wd        25572 non-null  float64       
 11  date_posted   51525 non-null  datetime64[ns]
 12  days_listed   51525 non-null  int64         
dtypes: Int64(2), datetime64[ns](1), float64(2), int64(2), object(6)
memory usage: 5.2+ MB


In [26]:
display(car_sales_df['is_4wd'].sample(20))

38755    NaN
14063    1.0
39806    NaN
37406    NaN
12096    NaN
7659     1.0
43957    1.0
6906     1.0
51475    1.0
14216    NaN
9132     NaN
17069    NaN
16929    1.0
48690    NaN
33717    NaN
27129    1.0
33923    NaN
7816     1.0
4070     NaN
10592    NaN
Name: is_4wd, dtype: float64

**Concerns:** Column "is_4wd" seems to only have 2 values "1.0" or "NaN". I can only assume that the "1.0" means yes and the not a number means no. If thats the case I should mark 0 for no and 1 for yes.

In [27]:
# Replace NaN values in 'is_4wd' column with 0
car_sales_df["is_4wd"].fillna(0, inplace=True)

# Convert the column to integers so '1.0' can to become '1' (integer)
car_sales_df["is_4wd"] = car_sales_df["is_4wd"].astype(int)

In [28]:
display(car_sales_df["is_4wd"].sample(20))

17563    1
23438    0
2437     0
27370    0
32259    0
20214    0
21204    1
1017     1
35259    1
8895     1
8163     1
31097    0
47971    1
22420    1
36024    0
38918    1
37608    1
51355    0
5178     0
50066    1
Name: is_4wd, dtype: int64

In [30]:
# Feature Engineering: Age of car
current_year = datetime.datetime.now().year
car_sales_df["car_age"] = current_year - car_sales_df["model_year"]

# Display the first few rows to confirm the changes
car_sales_df[["model_year", "car_age"]].head(10)

model_year  car_age
0        2011       12
1        <NA>     <NA>
2        2013       10
3        2003       20
4        2017        6
5        2014        9
6        2015        8
7        2013       10
8        2012       11
9        2008       15

In [32]:
car_age_distribution_df = car_sales_df["car_age"].value_counts().sort_index()

# Display the distribution
display(car_age_distribution_df.sample(10))

car_age
54      10
65       2
19    1722
46      13
45      15
51       5
17    2234
7     2954
75       1
38      18
Name: count, dtype: Int64

In [35]:
average_car_age_by_type = (
    car_sales_df.groupby("type")["car_age"].mean().reset_index()
)

display(average_car_age_by_type)

type    car_age
0           SUV  13.232109
1           bus  15.416667
2   convertible  20.644391
3         coupe  15.265987
4     hatchback  12.913758
5      mini-van  13.088372
6       offroad  17.833333
7         other  15.175214
8        pickup  13.656385
9         sedan  12.258978
10        truck  13.281757
11          van  13.267677
12        wagon  13.243885

In [42]:
# Plot distribution of car_age by type
fig = px.bar(
    average_car_age_by_type, x="type", y="car_age", title="Average Car Age by Type"
)
fig.update_layout(xaxis_title="Car Type", yaxis_title="Average Age (Years)")
fig.show()

**Car Age Distribution:** The bar chart of car ages by type revealed that most cars in the dataset fall within a certain age range, with the majority being around 10 to 15 years old.

#### Price Distribution

In [50]:
car_sales_df["price_length"] = car_sales_df["price"].astype(str).str.len()

# Filter rows where the length of 'price' is greater than 1
valid_price_data = car_sales_df[car_sales_df["price_length"] > 1]

# Calculate average price for each car type
average_price_by_type = valid_price_data.groupby("type")["price"].mean().reset_index()

# Display the resulting DataFrame
display(average_price_by_type)

type         price
0           SUV  11381.504279
1           bus  17135.666667
2   convertible  14944.441379
3         coupe  14829.925976
4     hatchback   6928.058767
5      mini-van   8207.314064
6       offroad  14292.294393
7         other  11032.807843
8        pickup  16075.812464
9         sedan   7047.101307
10        truck  17132.924747
11          van  10820.418152
12        wagon   9088.134328

In [49]:
# Plot the average price by car type 
fig = px.bar(
    average_price_by_type,
    x="type",
    y="price",
    title="Average Price by Car Type",
    labels={"price": "Average Price", "type": "Car Type"},
)
fig.show()

**Average Price by Car Type:** The average prices provide insights into the varying cost structures associated with different car types. Buyers can consider these averages when making decisions based on their budget and preferences.<br>

1. **SUV**: $11,381.50
   - SUVs have an average price of $11,381, making them a relatively affordable choice.
   
2. **Bus**: $17,135.67
   - Buses have a higher average price of $17,135, suggesting they may be more expensive due to their specific functionalities.

3. **Convertible**: $14,944.44
   - Convertibles have an average price of $14,944, reflecting the added cost associated with the convertible feature.

4. **Coupe**: $14,829.93
   - Coupes show a similar average price to convertibles, indicating that the body style may contribute to pricing.

5. **Hatchback**: $6,928.06
   - Hatchbacks have a notably lower average price of $6,928, making them a budget-friendly option.

6. **Mini-van**: $8,207.31
   - Mini-vans have an average price of $8,207, aligning with their family-oriented and practical design.

7. **Offroad**: $14,292.29
   - Offroad vehicles have an average price of $14,292, possibly reflecting the cost of specialized offroad features.

8. **Other**: $11,032.81
   - The 'Other' category has an average price of $11,033, encompassing various types with moderate pricing.

9. **Pickup**: $16,075.81
   - Pickups have a relatively high average price of $16,076, likely due to their versatility and capabilities.

10. **Sedan**: $7,047.10
    - Sedans have a lower average price of $7,047, making them an economical choice for many buyers.

11. **Truck**: $17,132.92
    - Trucks have a higher average price of $17,133, suggesting that their robustness and capabilities contribute to pricing.

12. **Van**: $10,820.42
    - Vans have an average price of $10,820, indicating a moderate price range.

13. **Wagon**: $9,088.13
    - Wagons have an average price of $9,088, falling within a reasonable price range.


#### Price vs. Odometer

In [17]:
alt.data_transformers.enable("default", max_rows=None)

# Price vs. Odometer Relationship
scatterplot = (
    alt.Chart(car_sales_df)
    .mark_circle()
    .encode(x="odometer", y="price", tooltip=["odometer", "price", "model", "condition"])
    .properties(title="Price vs. Odometer Relationship", width=600, height=400)
)

scatterplot.interactive()

alt.Chart(...)

In [62]:
# Drop rows with missing values in 'odometer'
selected_df = car_sales_df.dropna(subset=["odometer"])

# Extract 'price' and 'odometer' columns
price = selected_df["price"]
odometer = selected_df["odometer"]

# Calculate the correlation and p-value
correlation, p_value = pearsonr(price, odometer)

print(f"Correlation between price and odometer: {correlation}")
print(f"P-value: {p_value}")

Correlation between price and odometer: -0.42029896233720876
P-value: 0.0


**Price vs. Odometer**<br>
The correlation coefficient between price and odometer is approximately -0.42. A negative correlation suggests that as one variable (odometer) increases, the other variable (price) tends to decrease. This indicates that vehicles with higher mileage (odometer reading) generally have lower prices.

The p-value being 0.0 indicates that the correlation is statistically significant, meaning it's unlikely to have occurred by random chance.

In [78]:
car_sales_df["price_length"] = car_sales_df["price"].astype(str).str.len()

# Filter rows where the length of 'price' is greater than 1
valid_data = car_sales_df[car_sales_df["price_length"] > 1]

# Assuming 'days_listed' is the column representing the number of days a car was listed
top_20_shortest_listed = valid_data.nsmallest(20, "days_listed")

# Display the resulting DataFrame
top_20_shortest_listed[
    ["model", "days_listed", "price", "type", "condition", "date_posted", "odometer"]
]

model  days_listed  price       type  condition  \
1247     chevrolet silverado 1500            0  14995      truck  excellent   
1711   chevrolet silverado 2500hd            0  59589      truck  excellent   
1983                    ford f250            0  14000      truck  excellent   
2883                     ram 1500            0   4000      truck  excellent   
3965           chevrolet corvette            0  16750  hatchback   like new   
4567               toyota corolla            0   5000      sedan       good   
4901                     ram 1500            0  12500      truck       good   
6114                 dodge dakota            0    500     pickup       fair   
6548                honda odyssey            0   4800   mini-van       good   
7036   jeep grand cherokee laredo            0   5900        SUV  excellent   
9607                nissan sentra            0   4999      sedan  excellent   
9732                   ford f-150            0  15000      truck       good   
10722         chevrolet silverado            0   3100      truck       good   
12869                 honda pilot            0  21997        SUV  excellent   
14088             gmc sierra 1500            0  10500     pickup  excellent   
14446                   ford f250            0  17995      truck       good   
16046                honda accord            0   8200      sedan  excellent   
16138                    kia soul            0   3650  hatchback       good   
16210              toyota 4runner            0  13995        SUV  excellent   
16612        ford f250 super duty            0  11900     pickup       good   

      date_posted  odometer  
1247   2018-05-15     93300  
1711   2019-01-13      <NA>  
1983   2018-09-27    137500  
2883   2018-08-13    250000  
3965   2018-10-14     24540  
4567   2018-07-11    223000  
4901   2018-05-11     99892  
6114   2018-10-31    215457  
6548   2018-09-25    152400  
7036   2018-07-21      <NA>  
9607   2019-03-26    125000  
9732   2018-09-21     90048  
10722  2018-07-06    211000  
12869  2019-03-04     37093  
14088  2019-02-06      <NA>  
14446  2018-09-09     75465  
16046  2018-05-31    121000  
16138  2019-01-27      <NA>  
16210  2018-07-17      <NA>  
16612  2018-06-18    120971

In [79]:
# Assuming 'days_listed' is the column representing the number of days a car was listed
top_20_longest_listed = valid_data.nlargest(20, "days_listed")

# Display the resulting DataFrame
top_20_longest_listed[
    ["model", "days_listed", "price", "type", "condition", "date_posted", "odometer"]
]

model  days_listed  price       type  condition  \
4360          chevrolet impala          271   5200      sedan   like new   
28756             nissan versa          267   5500  hatchback  excellent   
2224                ford f-250          263   5995      truck       good   
51                  ford focus          261   3800      sedan       good   
7875             nissan altima          256   8980      coupe  excellent   
46583              ford fusion          252  11500      sedan  excellent   
3202              toyota prius          244   5995  hatchback  excellent   
24527              toyota rav4          243   5995        SUV       good   
19763  jeep wrangler unlimited          240  31995      wagon  excellent   
11698         chevrolet impala          236  21995      sedan   like new   
14977  jeep wrangler unlimited          233  12200    offroad       good   
3243              honda accord          228   6900      sedan       good   
16828           subaru outback          226   9995      wagon  excellent   
24507               ford f-150          225  11444     pickup  excellent   
34302           hyundai sonata          223   1500      sedan       good   
16207            toyota tundra          221  30898      truck  excellent   
50681           toyota corolla          221  12985      sedan  excellent   
30457            toyota tundra          217  16000     pickup       good   
39444           subaru impreza          213   3950      sedan       good   
30688                 ram 2500          210  38900      truck   like new   

      date_posted  odometer  
4360   2018-05-24    122000  
28756  2019-01-08     96000  
2224   2019-01-24    103000  
51     2018-11-29    130323  
7875   2019-02-02    101611  
46583  2019-03-06     65000  
3202   2018-10-17    130000  
24527  2018-06-29    106000  
19763  2018-11-16      <NA>  
11698  2019-02-24      <NA>  
14977  2018-05-16      <NA>  
3243   2018-07-21     80000  
16828  2019-04-11    116730  
24507  2018-08-06    160000  
34302  2018-09-14    138000  
16207  2018-05-04     66337  
50681  2018-11-09     34871  
30457  2018-12-18    168000  
39444  2019-01-10    111000  
30688  2019-04-02     74100

In [80]:
# Concatenate the top and bottom 20 listed cars
top_and_bottom_cars = pd.concat([top_20_shortest_listed, top_20_longest_listed])

# Convert categorical columns to numerical using one-hot encoding
top_and_bottom_cars_encoded = pd.get_dummies(
    top_and_bottom_cars, columns=["condition", "type"]
)

# Calculate the correlation matrix
correlation_matrix = top_and_bottom_cars_encoded[["price", "days_listed"]].corr()

# Display the correlation matrix
print("Correlation Matrix:")
print(correlation_matrix)

Correlation Matrix:
                price  days_listed
price        1.000000    -0.024338
days_listed -0.024338     1.000000


**Top 20 Shortest Listed vs. Top 20 Longest Listed Conclusion**<br>
- The correlation coefficient is approximately -0.024, indicating a very weak negative correlation between the price of a car and the number of days it is listed. In other words, there's a minimal tendency for lower-priced cars to have slightly longer listing durations and higher-priced cars to have slightly shorter listing durations.

### Relationship with car type vs odometer values

In [70]:
type_vs_odometer_df = (
    car_sales_df.dropna(subset=["odometer"])
    .groupby("type")["odometer"]
    .mean()
    .reset_index()
)

# Display the DataFrame
display(type_vs_odometer_df)

type       odometer
0           SUV  118312.160118
1           bus  114198.173913
2   convertible    84189.53562
3         coupe   78367.868059
4     hatchback  111066.444934
5      mini-van  127968.242211
6       offroad  121516.791444
7         other  107939.748879
8        pickup  120877.717388
9         sedan   107853.60792
10        truck  123228.543644
11          van  124701.476768
12        wagon  123748.181331

In [71]:
# Relationship with car type vs odometer values
fig = px.scatter(
    type_vs_odometer_df,
    x="type",
    y="odometer",
    title="Average Odometer Reading by Car Type",
    labels={"odometer": "Average Odometer Reading", "type": "Car Type"},
    template="plotly_white",
)

# Update the layout for better readability
fig.update_layout(showlegend=False, xaxis={"categoryorder": "total descending"})

# Show the plot
fig.show()

**Conclusion**<br>
- **SUV:** The average odometer reading is relatively high, indicating that SUVs may have covered a significant distance on average.

- **Bus:** Buses also have a high average odometer reading, suggesting that they might be used for longer trips or have been on the road for an extended period.

- **Convertible:** Convertibles show a lower average odometer reading compared to SUVs and buses, indicating potentially less usage or shorter trips.

- **Coupe:** Coupes have a moderate average odometer reading, falling between convertibles and hatchbacks.

- **Hatchback:** Hatchbacks have a relatively high average odometer reading, similar to SUVs, indicating that they might be commonly used for various purposes.

- **Mini-van:** Mini-vans have the highest average odometer reading among all car types, suggesting they are frequently used for family activities or longer journeys.

- **Offroad:** Offroad vehicles have a high average odometer reading, indicating that they might have been used for adventurous activities.

- **Other:** The 'Other' category has a moderate average odometer reading, encompassing various types with varied usage patterns.

- **Pickup:** Pickups show a high average odometer reading, similar to SUVs and trucks, suggesting versatility in usage.

- **Sedan:** Sedans have a moderate average odometer reading, falling between coupes and hatchbacks.

- **Truck:** Trucks have a high average odometer reading, indicating that they might be used for heavy-duty purposes.

- **Van:** Vans have a high average odometer reading, similar to SUVs and trucks, suggesting potential commercial or heavy usage.

- **Wagon:** Wagons have a high average odometer reading, similar to SUVs and trucks, indicating versatile usage.


#### Type vs. Days Listed

In [73]:
type_vs_days_listed_df = car_sales_df.groupby('type')['days_listed'].sum().reset_index()
display(type_vs_days_listed_df)

type  days_listed
0           SUV       493482
1           bus         1044
2   convertible        17480
3         coupe        90643
4     hatchback        42439
5      mini-van        45743
6       offroad         8645
7         other         9795
8        pickup       274513
9         sedan       479172
10        truck       486826
11          van        25760
12        wagon        62517

In [75]:
fig = px.scatter(
    type_vs_days_listed_df,
    x="type",
    y="days_listed",
    title="Days Listed by Car Type",
    labels={"days_listed": "Days Listed", "type": "Car Type"},
    template="plotly_white",
)

# Update the layout for better readability
fig.update_layout(showlegend=False, xaxis={"categoryorder": "total descending"})

# Show the plot
fig.show()

**Conclusion**
- Understanding the average days listed for each car type can be useful for sellers and buyers alike. Sellers can adjust their expectations based on the typical duration, while buyers may gauge the availability and demand for specific car types in the market.
    - **SUV, Pickup, Truck:** SUVs, pickups, and trucks have the highest number of days listed. This may suggest that these types of vehicles, often used for various purposes, take longer to find buyers.

    - **Bus, Convertible, Offroad:** Buses, convertibles, and offroad vehicles have relatively lower days listed. Buses may have a niche market, while convertibles and offroad vehicles might attract more specific buyers.

    - **Sedan, Wagon, Hatchback:** Sedans, wagons, and hatchbacks show moderate days listed. These car types are commonly used for daily commuting, potentially leading to a balanced demand and supply.

    - **Coupe:** Coupes have a significant number of days listed, indicating that they might take longer to find buyers compared to other car types.

    - **Van:** Vans have a moderate number of days listed, suggesting a balanced market for this type.

    - **Other:** The 'Other' category has a relatively short duration, indicating that less common car types may find buyers more quickly.

## The Average Car Posted Each Month

In [76]:
car_sales_df["month_posted"] = car_sales_df["date_posted"].dt.month_name()

# Group by month and type, count the number of postings
monthly_posting_counts = (
    car_sales_df.groupby(["month_posted", "type"]).size().reset_index(name="count")
)

# Find the car type posted the most in each month
most_posted_by_month = monthly_posting_counts.loc[
    monthly_posting_counts.groupby("month_posted")["count"].idxmax()
]

display(most_posted_by_month)

month_posted   type  count
0          April    SUV    684
23        August  truck   1122
26      December    SUV   1120
48      February  truck    997
60       January  sedan   1074
74          July  truck   1093
87          June  truck   1019
90         March    SUV   1185
103          May    SUV   1098
115     November    SUV   1084
137      October  sedan   1136
150    September  sedan   1076

In [77]:
# Plot the distribution
fig = px.bar(
    most_posted_by_month,
    x="month_posted",
    y="count",
    color="type",
    labels={"count": "Number of Postings"},
    title="Most Posted Car Type in Each Month",
)

fig.show()

**Observations**<br>
- **SUV Dominance:** SUVs appear to be the most posted car type in several months, including April, December, March, May, and November.

- **Truck Dominance:** Trucks dominate in months like August, February, July, and June.

- **Sedan Peaks:** Sedans have a significant presence in months like January, October, and September.